In [251]:
import pandas as pd
import networkx as nx
import matplotlib.pyplot as plt
import numpy as np

In [224]:
df = pd.read_csv('world_cup_matches.csv', encoding='cp1252')

In [225]:
df[df["Match Name"] == "Sweden v Brazil"]

Key Id Tournament Id      tournament Name   Match Id       Match Name  \
513     514       WC-1994  1994 FIFA World Cup  M-1994-50  Sweden v Brazil   

      Stage Name      Group Name  Group Stage  Knockout Stage  Replayed  ...  \
513  semi-finals  not applicable            0               1         0  ...   

     Away Team Score Margin Extra Time Penalty Shootout Score Penalties  \
513                       1          0                0             0-0   

    Home Team Score Penalties Away Team Score Penalties         Result  \
513                         0                         0  away team win   

    Home Team Win Away Team Win Draw  
513             0             1    0  

[1 rows x 37 columns]

In [226]:
df.head()

Key Id Tournament Id      tournament Name   Match Id  \
0       1       WC-1930  1930 FIFA World Cup  M-1930-01   
1       2       WC-1930  1930 FIFA World Cup  M-1930-02   
2       3       WC-1930  1930 FIFA World Cup  M-1930-03   
3       4       WC-1930  1930 FIFA World Cup  M-1930-04   
4       5       WC-1930  1930 FIFA World Cup  M-1930-05   

                Match Name   Stage Name Group Name  Group Stage  \
0          France v Mexico  group stage    Group 1            1   
1  United States v Belgium  group stage    Group 4            1   
2      Yugoslavia v Brazil  group stage    Group 2            1   
3           Romania v Peru  group stage    Group 3            1   
4       Argentina v France  group stage    Group 1            1   

   Knockout Stage  Replayed  ...  Away Team Score Margin Extra Time  \
0               0         0  ...                      -3          0   
1               0         0  ...                      -3          0   
2               0         0  ...                      -1          0   
3               0         0  ...                      -2          0   
4               0         0  ...                      -1          0   

  Penalty Shootout Score Penalties Home Team Score Penalties  \
0                0             0-0                         0   
1                0             0-0                         0   
2                0             0-0                         0   
3                0             0-0                         0   
4                0             0-0                         0   

  Away Team Score Penalties         Result Home Team Win Away Team Win Draw  
0                         0  home team win             1             0    0  
1                         0  home team win             1             0    0  
2                         0  home team win             1             0    0  
3                         0  home team win             1             0    0  
4                         0  home team win             1             0    0  

[5 rows x 37 columns]

In [227]:
df.groupby("Match Name").size().reset_index(
    name='counts').sort_values(by='counts', ascending=False)

Match Name  counts
124          Brazil v Sweden       6
354           Italy v France       5
416  Netherlands v Argentina       5
100  Brazil v Czechoslovakia       5
109          Brazil v Mexico       5
..                       ...     ...
288        Germany v England       1
289          Germany v Ghana       1
290           Germany v Iran       1
291          Germany v Italy       1
758         Zaire v Scotland       1

[759 rows x 2 columns]

In [228]:
df['Match Date'] = pd.to_datetime(df['Match Date'])

In [229]:
df['Year'] = df['Match Date'].dt.year

In [230]:
teams = df.groupby('Home Team Name')['Year'].nunique()

In [231]:
teams = teams[teams > 5].index

In [232]:
teams

Index(['Argentina', 'Australia', 'Belgium', 'Brazil', 'Cameroon', 'Chile',
       'Costa Rica', 'Czechoslovakia', 'England', 'France', 'Germany',
       'Hungary', 'Italy', 'Japan', 'Mexico', 'Netherlands', 'Nigeria',
       'Paraguay', 'Poland', 'Portugal', 'Saudi Arabia', 'South Korea',
       'Soviet Union', 'Spain', 'Sweden', 'Switzerland', 'United States',
       'Uruguay', 'West Germany', 'Yugoslavia'],
      dtype='object', name='Home Team Name')

In [233]:
teams.size

30

In [234]:
filtered_df = df[(df['Home Team Name'].isin(teams)) &
                 (df['Away Team Name'].isin(teams))]

In [235]:
filtered_df.head()

Key Id Tournament Id      tournament Name   Match Id  \
0       1       WC-1930  1930 FIFA World Cup  M-1930-01   
1       2       WC-1930  1930 FIFA World Cup  M-1930-02   
2       3       WC-1930  1930 FIFA World Cup  M-1930-03   
4       5       WC-1930  1930 FIFA World Cup  M-1930-05   
5       6       WC-1930  1930 FIFA World Cup  M-1930-06   

                Match Name   Stage Name Group Name  Group Stage  \
0          France v Mexico  group stage    Group 1            1   
1  United States v Belgium  group stage    Group 4            1   
2      Yugoslavia v Brazil  group stage    Group 2            1   
4       Argentina v France  group stage    Group 1            1   
5           Chile v Mexico  group stage    Group 1            1   

   Knockout Stage  Replayed  ...  Extra Time Penalty Shootout Score Penalties  \
0               0         0  ...           0                0             0-0   
1               0         0  ...           0                0             0-0   
2               0         0  ...           0                0             0-0   
4               0         0  ...           0                0             0-0   
5               0         0  ...           0                0             0-0   

  Home Team Score Penalties Away Team Score Penalties         Result  \
0                         0                         0  home team win   
1                         0                         0  home team win   
2                         0                         0  home team win   
4                         0                         0  home team win   
5                         0                         0  home team win   

  Home Team Win Away Team Win Draw  Year  
0             1             0    0  1930  
1             1             0    0  1930  
2             1             0    0  1930  
4             1             0    0  1930  
5             1             0    0  1930  

[5 rows x 38 columns]

In [296]:
worldcup_edges = filtered_df[["Match Name",
                              "Home Team Name", "Away Team Name"]]

In [297]:
worldcup_edges["pair"] = df.apply(lambda row: " v ".join(
    sorted([row["Home Team Name"], row["Away Team Name"]])), axis=1)

/tmp/ipykernel_5021/3099048731.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  worldcup_edges["pair"] = df.apply(lambda row: " v ".join(


In [298]:
worldcup_edges = worldcup_edges.groupby("pair").size().reset_index()

In [299]:
worldcup_edges[['source', 'target']
               ] = worldcup_edges['pair'].str.split(' v ', expand=True)

In [300]:
worldcup_edges = worldcup_edges.drop(columns=['pair'])

In [301]:
worldcup_edges = worldcup_edges.rename(
    columns={0: 'weight'}).reset_index(drop=True)

In [302]:
worldcup_edges.sort_values("weight", ascending=False)

weight          source       target
69        7          Brazil       Sweden
13        6       Argentina  Netherlands
268       5    West Germany   Yugoslavia
62        5          Brazil       Mexico
14        5       Argentina      Nigeria
..      ...             ...          ...
118       1  Czechoslovakia      Uruguay
120       1  Czechoslovakia   Yugoslavia
122       1         England      Germany
123       1         England      Hungary
134       1         England  Switzerland

[269 rows x 3 columns]

In [303]:
got_graph = nx.from_pandas_edgelist(
    worldcup_edges, "source", "target", edge_attr="weight")
weights = np.array([e[2]["weight"] for e in got_graph.edges(data=True)])
max_weight = np.max(weights)

In [304]:
weights

array([1, 3, 4, 1, 1, 1, 5, 4, 3, 3, 5, 1, 4, 6, 5, 3, 1, 2, 1, 1, 2, 2,
       1, 2, 4, 1, 1, 2, 2, 1, 1, 1, 1, 1, 1, 2, 4, 3, 2, 1, 1, 2, 3, 2,
       2, 1, 1, 3, 3, 2, 2, 1, 3, 4, 3, 5, 4, 4, 2, 2, 5, 1, 5, 5, 4, 2,
       1, 2, 5, 7, 3, 1, 2, 4, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       3, 1, 1, 2, 3, 2, 1, 3, 1, 1, 2, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 2,
       1, 1, 3, 1, 1, 2, 1, 1, 1, 2, 1, 3, 2, 2, 3, 1, 3, 3, 4, 1, 2, 5,
       4, 1, 2, 2, 1, 1, 1, 1, 1, 2, 4, 3, 2, 2, 1, 1, 2, 1, 1, 2, 1, 3,
       3, 3, 2, 3, 1, 1, 2, 1, 1, 1, 2, 2, 1, 1, 2, 1, 3, 1, 1, 2, 3, 2,
       1, 3, 2, 3, 3, 3, 4, 1, 1, 1, 1, 1, 2, 1, 2, 1, 1, 2, 1, 1, 2, 1,
       1, 2, 2, 1, 1, 1, 1, 1, 2, 1, 1, 1, 2, 3, 1, 1, 1, 1, 1, 1, 2, 1,
       1, 1, 1, 1, 2, 1, 1, 1, 1, 2, 3, 1, 1, 1, 3, 1, 1, 2, 1, 1, 1, 3,
       2, 2, 3, 1, 2, 2, 2, 1, 2, 1, 3, 2, 1, 1, 1, 1, 2, 1, 1, 2, 1, 1,
       2, 3, 2, 5, 1])

In [305]:
max_weight

7

In [306]:
# pomocniczy wykres do ustalenia legendy szerokości krawędzi
plt.hist(weights, bins=30)
plt.show()

In [307]:
pos = nx.circular_layout(got_graph)

In [310]:
ig, ax = plt.subplots(1, 1, figsize=(16, 16), dpi=300)

ax.set_title(
    "Countries Playing with Each Other in FIFA World Cup 1930-2022", fontsize=24)
ax.text(0.5, 0.98, "Countries With 5+ World Cup Appearances",
        fontsize=17, ha="center", transform=ax.transAxes)

nx.draw_networkx_nodes(got_graph,
                       pos=pos,
                       node_size=100,
                       node_color="#2C6B4F",
                       ax=ax
                       )

nx.draw_networkx_edges(
    got_graph,
    pos=pos,
    width=np.sqrt(weights / max_weight) * 10,
    edge_color="#729762",
    alpha=0.5,
    ax=ax,
)

for i, (node, (x, y)) in enumerate(pos.items()):
    ax.text(x, y - 0.03, node, fontsize=11, ha="center", va="center")

for w in [1, 2, 3, 4, 5, 6, 7]:
    ax.plot([], [], "#729762", linewidth=np.sqrt(
        w) / np.sqrt(max_weight) * 10, label=w)
ax.legend(title="Number of Matches", frameon=False,
          bbox_to_anchor=(-0.05, 0), loc="lower left", fontsize=11, title_fontsize=17)
plt.axis("off")
# plt.savefig('WorldCupGames.jpg', format='jpg', dpi=300)
plt.show()